# Summariser project

This is my summariser code project. It is a work in progress.

## Step one: text extraction
First we try to extract text from stakeholder submissions. This can be a tricky process, particularly where there is handwritten/illegible text. PDFs are not that friendly for text extraction.

- I have manually downloaded submissions from the APH website and saved them in one folder on my desktop.
- *Note*: some submissions come with appendixes/attachments which are not strictly necessary to understanding the key points being made by the stakeholder and can add hundreds of pages. To control cost and to fit within the current context window of 8k tokens, I have 'preprocessed' some PDFs to delete attachments.

In [11]:
import os
import pdfplumber
import openai
from datetime import datetime
import json
import pandas as pd
import ast
from IPython.display import display, HTML
import re
import tiktoken


# Directory with PDF files
pdf_dir = '/users/arseny/Desktop/testsubmissions'

# Create a timestamp string
timestamp = datetime.now().strftime('%Y%m%d%H%M')

# Data list
data = []

# Token counter

encoding = tiktoken.encoding_for_model('gpt-4') # Replace with other model if not using GPT-4

# Function to remove illegal characters
def remove_illegal_chars(text):
    ILLEGAL_CHARACTERS_RE = re.compile(r'[\000-\010]|[\013-\014]|[\016-\037]')
    text = ILLEGAL_CHARACTERS_RE.sub(r'', text)
    return text

    # Loop over the PDF files in the directory
for file_name in os.listdir(pdf_dir):
    if file_name.endswith('.pdf'):
        file_path = os.path.join(pdf_dir, file_name)
            
        # Open the PDF file
        with pdfplumber.open(file_path) as pdf_file:
                
            # Initialize an empty string for the text
            text = ''

            # Loop over the pages and add the text to the string
            for i,  page in enumerate(pdf_file.pages):
                try:
                    page_text = page.extract_text()
                    page_text = remove_illegal_chars(page_text)
                    text += page_text
                    
                except Exception as e:
                    print(f"For {file_name},failed to extract text from page {i} with error: {str(e)}")
            
            # Count the pages
            page_count = len(pdf_file.pages)
            
            # Count the words
            word_count = len(text.split())
            
            # Number of tokens
            num_tokens = len(encoding.encode(text))
  
            # Append to data
            data.append([file_name, page_count, word_count, text, num_tokens])
            

# Convert to DataFrame
df = pd.DataFrame(data, columns=['File','Page count', 'Word count', 'Text', 'Tokens'])


## Step two: 'cleaning' the data
For some of the submissions, the program is likely to fail at extracting text due to illegibility/formatting of the PDFs (e.g. for regional bank closure submissions, for about 110 of 500ish submissions the text extraction failed).

We can try to improve the success rate by experimenting with different extraction methods in Python or with professional OCR software. In due course, AI software is likely to improve the success rate (GPT-4 is capable of taking images as input - this capability has not been publicly released yet).

In the meantime, it is better to filter out submissions where only nonsense text or header/footer text has been extracted as these will result in spurious summaries in the next step. 

Currently this is pretty easy to do through manual inspection of extracted text. But should be able to at least partially automate by filtering for number of words extracted and calling LLM to categorise whether actual text is extracted or if it is nonsense/just the headers & footers.

In [14]:
# Sort by word count in ascending order
df.sort_values('Word count', ascending=True, inplace=True)

In [21]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', 150)
df[['Text', 'Word count']].head(150)

Text   
419                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

## Step three: summarisation
The next step involves making an API call to the LLM and prompting it to summarise the text from each submission (along with some other inference e.g. asking it to rate the sentiment of the submission).

- Currently can fail for longer submissions. This will be fixed with longer LLM context windows (I'm awaiting access to the Claude API which will allow 100,000 tokens -- approx 75,000 words). 
- Can also partially fix by splitting up longer documents, summarising the chunks and then getting the LLM to combine those summaries. A bit fiddly and a worse result than having the entire context considered as one.

In [ ]:
# API key

from dotenv import load_dotenv, find_dotenv
_ = load_dotenv(find_dotenv()) # read local .env file

openai.api_key  = os.environ['OPENAI_API_KEY']

# Create summariser function

def get_completion(prompt, model="gpt-4"): 
    messages = [{"role": "user", "content": prompt}]
    response = openai.ChatCompletion.create(
        model=model,
        messages=messages,
        temperature=0, 
    )
    return response.choices[0].message["content"]

# Load the dataframe from Excel
df = pd.read_excel(f'submission_text_extracts_checked{timestamp}.xlsx')

# Initialise data list for summaries
summary_data = []

    # Loop over the rows in the DataFrame
for idx, row in df.iterrows():
    if row['ManualSummary'] != 'Yes':
        text = row['Text']
        file_name = row['File']
        page_count = row['Page count']
        

        # Summarize the text

        prompt = f"""Your task is to perform the following actions as if you are a highly experienced, knowledgeable Australian Government policy adviser who is known for their clear thinking and writing:
        1. Summarise the following public submission extracted below.
        2. Extract the key policy ideas, if any, raised in the submission.
        3. Extract the key concerns, if any, raised in the submission.
        4. Categorise the author as 'individual' (including more than one individual), 'government', 'business', 'other' or 'unsure'. No commentary, just the category. 
        5. On a scale of 1 to 10, rank the sentiment of the text towards the Government's current policy settings or proposals (1 being very negative and 10 being very positive). No need for commentary, just the number.
        6. Output a json object that contains the following keys corresponding to the above tasks: summary, ideas, concerns, category, sentiment.
        Only produce output for step 6 - the JSON object should incorporate the previous answers.

                   
        Here is the submission text: [{text}]"""
            
        try:
            response = get_completion(prompt)
            print(response)
            
        except:
            summary = ideas = concerns = category = sentiment = 'Error: Could not generate OpenAI response'
            summary_data.append([file_name, summary, ideas, concerns, category, sentiment, page_count, text])
            continue

        # Parse the response as JSON

        try:
            response_json = json.loads(response)

            # Extract the fields

            summary = response_json.get('summary', 'Error: could not parse response')
            ideas = response_json.get('ideas', 'Error: could not parse response')
            concerns = response_json.get('concerns', 'Error: could not parse response')
            category = response_json.get('category', 'Error: could not parse response')
            sentiment = response_json.get('sentiment', 'Error: could not parse response')
        except json.JSONDecodeError:
            summary = ideas = concerns = category = sentiment = 'Error: could not parse response'
                
        # Append to data
        summary_data.append([file_name, summary, ideas, concerns, category, sentiment, page_count, text])
        
        # Print the count
        print(f'Summarised submission: {idx+1}')

# Convert to DataFrame
summary_df = pd.DataFrame(summary_data, columns=['File', 'Summary', 'Ideas', 'Concerns', 'Category', 'Sentiment (out of 10)', 'Page count', 'Text'])

# Write to Excel
summary_df.to_excel(f'summaries_{timestamp}.xlsx', index=False)


## Step four: formatting output
*In progress - need to clean up the code here*.

Post-processing of output to make it prettier (e.g. converting lists of ideas/concerns to bullet point lists).

In [ ]:
# Load the Excel file
df = pd.read_excel(f'summaries_{timestamp}.xlsx')

# Transform 'ideas' and 'concerns' from string representation of list to actual list
df['Ideas'] = df['Ideas'].apply(lambda x: ast.literal_eval(x))
df['Concerns'] = df['Concerns'].apply(lambda x: ast.literal_eval(x))

# Convert lists to bullet points
df['Ideas'] = df['Ideas'].apply(lambda ideas: "\n".join(f'• {idea}' for idea in ideas))
df['Concerns'] = df['Concerns'].apply(lambda concerns: "\n".join(f'• {concern}' for concern in concerns))

# Set pandas to display the full content of the columns
pd.set_option('display.max_colwidth', None)

# Convert the DataFrame to HTML
df_html = df.to_html().replace("\\n","<br>")

# Add a style tag to the HTML to align text in the 'Summary', 'Concerns', and 'Ideas' columns to the left
styles = """
<style>
    table.dataframe th[scope="col"]:nth-of-type(2),
    table.dataframe th[scope="col"]:nth-of-type(3),
    table.dataframe th[scope="col"]:nth-of-type(4),
    table.dataframe td:nth-of-type(2),
    table.dataframe td:nth-of-type(3),
    table.dataframe td:nth-of-type(4)
    {
        text-align: left !important;
    }
</style>
"""

# Display the HTML with the added styles
display(HTML(styles + df_html))


In [ ]:
# Save the DataFrame to a new Excel file
df.to_excel(f"transformed_summaries_{timestamp}.xlsx", index=False)


In [ ]:
# Load the Excel file
df = pd.read_excel(f'summaries_{timestamp}_v2.xlsx')

# Transform 'ideas' and 'concerns' from string representation of list to actual list
df['Ideas'] = df['Ideas'].apply(lambda x: ast.literal_eval(x))
df['Concerns'] = df['Concerns'].apply(lambda x: ast.literal_eval(x))

# Convert lists to bullet points
df['Ideas'] = df['Ideas'].apply(lambda ideas: "\n".join(f'• {idea}' for idea in ideas))
df['Concerns'] = df['Concerns'].apply(lambda concerns: "\n".join(f'• {concern}' for concern in concerns))

In [ ]:
# Set pandas to display the full content of the columns
pd.set_option('display.max_colwidth', None)

# Convert the DataFrame to HTML
df_html = df.to_html().replace("\\n","<br>")

# Add a style tag to the HTML to align text in the 'Summary', 'Concerns', and 'Ideas' columns to the left
styles = """
<style>
    table.dataframe th[scope="col"]:nth-of-type(2),
    table.dataframe th[scope="col"]:nth-of-type(3),
    table.dataframe th[scope="col"]:nth-of-type(4),
    table.dataframe td:nth-of-type(2),
    table.dataframe td:nth-of-type(3),
    table.dataframe td:nth-of-type(4)
    {
        text-align: left !important;
    }
</style>
"""

# Display the HTML with the added styles
display(HTML(styles + df_html))

In [ ]:
summary_df.to_excel(f'summaries_{timestamp}_v3.xlsx')

## Step five: visualising the summaries
Experimenting with different ways of visualising data e.g. bar chart to show average sentiment for different stakeholder groups and separate word clouds for: extracted text, summaries, ideas and concerns.

In [ ]:
import matplotlib.pyplot as plt
from wordcloud import WordCloud
import pandas as pd

# Excel file path
file_path = f"transformed_summaries_202306011742.xlsx"

# Load the data
df = pd.read_excel(file_path)

# Aggregating average sentiment for each author category
avg_sentiment = df.groupby('Category')['Sentiment (out of 10)'].mean()

# Creating bar chart
plt.figure(figsize=(10,6))
plt.bar(avg_sentiment.index, avg_sentiment.values)
plt.xlabel('Author Category')
plt.ylabel('Average Sentiment')
plt.title('Average Sentiment per Author Category')
plt.show()

# WordCloud generation function
def generate_wordcloud(text_series, title):
    # Convert all values in the series to strings before joining
    text = ' '.join(text_series.astype(str))
    wordcloud = WordCloud(width=800, height=400, max_words=100).generate(text)
    plt.figure(figsize=(10,5))
    plt.imshow(wordcloud, interpolation='bilinear')
    plt.title(title)
    plt.axis('off')
    plt.show()

# Generate word clouds for 'summary', 'ideas', and 'concerns'
generate_wordcloud(df['Summary'], 'Summary Word Cloud')
generate_wordcloud(df['Ideas'], 'Ideas Word Cloud')
generate_wordcloud(df['Concerns'], 'Concerns Word Cloud')
generate_wordcloud(df['Text'], 'Full Sub Text Word Cloud')

## Debugging
Ignore this section - was debugging why extracted text was cutting off in Excel (turns out there are word/character limits on text per cell). Excel not good for storing lots of text -- will consider using SQLite database or CSV file.

In [8]:
# Get the row for the specific file
row = df[df['File'] == 'Submission 357 - Per Capita.pdf']

# Get the extracted text
extracted_text = row['Text'].values[0]

print(f"Extracted text for 'Submission 357 - Per Capita.pdf' from DataFrame:\n{extracted_text}\n")

Extracted text for 'Submission 357 - Per Capita.pdf' from DataFrame:
Bank closures in regional Australia
Submission 357Bank closures in regional Australia
Submission 357
PER CAPITA DISCUSSION PAPER
Table of Contents
About Per Capita ............................................................................................................................................. 3
Executive Summary ......................................................................................................................................... 4
Introduction ..................................................................................................................................................... 5
The big picture: why public banking? ......................................................................................................... 5
The banking environment in Australia ............................................................................................................ 8
The his

In [9]:
# Write to Excel
excel_file = f'submission_text_extracts_{timestamp}.xlsx'
df.to_excel(excel_file, index=False)

# Read the Excel file
df_read = pd.read_excel(excel_file)

# Get the row for the specific file
row = df_read[df_read['File'] == 'Submission 357 - Per Capita.pdf']

# Get the extracted text
extracted_text = row['Text'].values[0]

print(f"Extracted text for 'Submission 357 - Per Capita.pdf' from Excel:\n{extracted_text}\n")

Extracted text for 'Submission 357 - Per Capita.pdf' from Excel:
Bank closures in regional Australia
Submission 357Bank closures in regional Australia
Submission 357
PER CAPITA DISCUSSION PAPER
Table of Contents
About Per Capita ............................................................................................................................................. 3
Executive Summary ......................................................................................................................................... 4
Introduction ..................................................................................................................................................... 5
The big picture: why public banking? ......................................................................................................... 5
The banking environment in Australia ............................................................................................................ 8
The history

### Trying to build a text splitter for the summariser
*In progress. Experimental code. Purpose is to handle larger submissions. Interim measure till get access to larger AI context windows.*

In [ ]:
        try:
            if #tokenlength < #X (maybe 7000?):
                response = get_completion(prompt)
                print(response)
            else:
                #split into chunks
                # summarise each chunk - perhaps with overlap
                #summarise the combined summaries
            response = get_completion(prompt)
            print(response)